# Base installs

In [1]:
import agentpy as ap
import numpy as np
import matplotlib.pyplot as plt
import IPython
import random

In [2]:
import socket
import time
from time import sleep

# Servidor

In [3]:
class Server:
    def send_message(message):
        try:
            s = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
            s.connect(('127.0.0.1', 1101))  # Usa el puerto correcto según Unity
            s.send(message.encode('ascii'))
            s.close()
        except Exception as e:
            print(f"Error sending to server: {e}")

# Paths de carros

In [4]:
# Paths de carros
class Path:
    def __init__(self, path_id, traffic_light_id, waypoints, turn_type):
        self.path_id = path_id
        self.traffic_light_id = traffic_light_id
        self.waypoints = waypoints
        self.turn_type = turn_type

    def get_next_position(self, current_waypoint_index):
        if current_waypoint_index < len(self.waypoints) - 1:
            return self.waypoints[current_waypoint_index + 1]
        return None

class ExtendedIntersection(ap.Grid):
    def __init__(self, model, shape):
        # Grilla extendida
        extended_size = shape[0] + 20  # +10 en cada dirección
        super().__init__(model, shape=(extended_size, extended_size))

        # Offset para manejar coordenadas negativas
        self.offset = 10
        self.visible_area = shape  # (30, 30) - área visible original

    def add_agents(self, agents, positions=None):
        """Manejar posiciones extendidas"""
        if positions:
            # Convertir posiciones con offset
            adjusted_positions = []
            for pos in positions:
                adjusted_pos = (pos[0] + self.offset, pos[1] + self.offset)
                adjusted_positions.append(adjusted_pos)
            super().add_agents(agents, adjusted_positions)
        else:
            super().add_agents(agents)

    def get_real_position(self, agent):
        """Obtener posición real (con coordenadas posiblemente negativas)"""
        grid_pos = self.positions[agent]
        return (grid_pos[0] - self.offset, grid_pos[1] - self.offset)

#Spawner de carros

In [5]:
# Spawner de carros
class EnhancedCarSpawner:
    def __init__(self, model):
        self.model = model
        # No necesitas self.server, solo usa Server.send_message directamente

        #Spawn zones MÁS ATRÁS (fuera del área visible)
        spawn_distance = 8  # Distancia desde el borde visible

        self.spawn_zones = {
            'north': [
                (12, self.model.p.size + spawn_distance),
                (11, self.model.p.size + spawn_distance),
                (13, self.model.p.size + spawn_distance)
            ],
            'west': [
                (-spawn_distance, 12),
                (-spawn_distance, 11),
                (-spawn_distance, 13)
            ],
            'south': [
                (16, -spawn_distance),
                (15, -spawn_distance),
                (17, -spawn_distance)
            ],
            'east': [
                (self.model.p.size + spawn_distance, 18),
                (self.model.p.size + spawn_distance, 17),
                (self.model.p.size + spawn_distance, 19)
            ]
        }

        # Spawn rates per direction
        self.spawn_rates = {
            'north': 0.12,
            'west': 0.10,
            'south': 0.15,
            'east': 0.08
        }

        # Route probabilities within each direction
        self.route_distributions = {
            'north': {1: 0.25, 2: 0.50, 3: 0.25},
            'west': {4: 0.30, 5: 0.45, 6: 0.25},
            'south': {7: 0.20, 8: 0.35, 9: 0.35, 10: 0.10},
            'east': {11: 0.35, 12: 0.40, 13: 0.25}
        }

    def get_available_spawn_position(self, direction):
        """Find an available spawn position in the given direction"""
        positions = self.spawn_zones[direction]

        for pos in positions:
            #Verificar disponibilidad sin restricción de grilla
            occupied = False
            for car in self.model.intersect.agents:
                car_pos = car.get_position()
                if np.linalg.norm(np.array(pos) - np.array(car_pos)) < 2:  # Mayor distancia
                    occupied = True
                    break

            if not occupied:
                return pos

        return None

    def select_path_for_direction(self, direction):
        """Randomly select a path based on direction probabilities"""
        routes = self.route_distributions[direction]
        paths = list(routes.keys())
        weights = list(routes.values())
        return random.choices(paths, weights=weights)[0]

    def spawn_cars(self):
        """Spawn cars con posiciones extendidas"""
        for direction, spawn_rate in self.spawn_rates.items():
            if random.random() < spawn_rate:
                spawn_pos = self.get_available_spawn_position(direction)

                if spawn_pos:
                    path_id = self.select_path_for_direction(direction)
                    path = self.model.paths[path_id]
                    traffic_light = self.model.traffic_lights[path.traffic_light_id]

                    car = EnhancedCar(self.model, path=path, traffic_light=traffic_light)

                    # Usar add_agents con posiciones extendidas
                    self.model.intersect.add_agents([car], positions=[spawn_pos])

                    msg = f"Spawn {path_id} ({path.turn_type}) from {direction} at {spawn_pos}$"
                    print(f"\t{msg}")
                    Server.send_message(msg)


# Traffic light agent

In [6]:
# Traffic light agent
class TrafficLight(ap.Agent):
    def setup(self, light_id, position, green_time, min_green_time, flash_time=2, yellow_time=3, red_buffer=3):
        self.light_id = light_id
        self.position = position
        self.state = 'red' # All lights get init to red

        # Light times
        self.green_time = green_time
        self.min_green_time = min_green_time # Once this base threshold passes, other cars can travel
        self.flash_time = flash_time
        self.yellow_time = yellow_time
        self.red_buffer = red_buffer # Just so all are stopped
        self.cycle_time = green_time + flash_time + yellow_time + red_buffer # Max cycle length

        # Active tracking
        self.timer = 0
        self.time_in_current_state = 0
        ## REDOING TIMERS
        self.time_in_state = 0

        # Adding to check if light should be active
        self.should_be_active = False

    # New redoing update states
    def update_state(self):
      self.time_in_state += 1 # Track time in the curr state

      # If it has to be active and currently red, start the green phase and just let it do it's thing
      if self.should_be_active and self.state == 'red':
          self.state = 'green'
          self.time_in_state = 0
          return

      # So just keeps the normal cycles going until reached the max time
      # G -> Flash
      if self.state == 'green':
          if self.time_in_state >= self.green_time:
            self.state = 'flash'
            self.time_in_state = 0

      # Flash -> Y
      elif self.state == 'flash':
          if self.time_in_state >= self.flash_time:
              self.state = 'yellow'
              self.time_in_state = 0

      # Y -> Red buffer
      elif self.state == 'yellow':
          if self.time_in_state >= self.yellow_time:
              self.state = 'red_buffer'
              self.time_in_state = 0

      # Red buffer -> red and keeps it there by deactivating it
      elif self.state == 'red_buffer':
          if self.time_in_state >= self.red_buffer:
              self.state = 'red'
              self.time_in_state = 0
              self.should_be_active = False # Deactivates it


    # Controller tells it to switch to flashing to go thru the rest of the cycle
    def force_switch(self):
          # Ensure it's green
          if self.state == 'green':
              self.state = 'flash'
              self.time_in_state = 0

    def cars_can_move(self):
        return self.state in ['green', 'flash']

    def should_slow_down(self):
        return self.state in ['yellow', 'red', 'red_buffer']

# Car agent

In [7]:
# Car agent
class EnhancedCar(ap.Agent):
    def setup(self, path, traffic_light):
        self.intersect = self.model.intersect
        self.path = path
        self.traffic_light = traffic_light
        self.current_waypoint_index = -1
        self.velocity = np.array([0, 0])
        self.max_speed = 1
        self.following_distance = 2
        self.headway_distance = 1.5


        '''# Define stop positions for each traffic light
        self.stop_positions = {
            1: (12, 24),
            2: (5, 12),
            3: (16, 7),
            4: (21, 18)
        }'''

        # Define la dirección de aproximación para cada semáforo
        self.approach_directions = {
            1: (0, -1),   # Light 1: Se aproxima desde el NORTE (hacia abajo)
            2: (1, 0),    # Light 2: Se aproxima desde el OESTE (hacia derecha)
            3: (0, 1),    # Light 3: Se aproxima desde el SUR (hacia arriba)
            4: (-1, 0)    # Light 4: Se aproxima desde el ESTE (hacia izquierda)
        }

    def get_position(self):
        """Usar posición real del ExtendedIntersection"""
        return self.intersect.get_real_position(self)

    def get_current_target(self):
        if self.current_waypoint_index == -1:
            return self.path.waypoints[0]
        if self.current_waypoint_index + 1 < len(self.path.waypoints):
            return self.path.waypoints[self.current_waypoint_index + 1]
        return None

    def calculate_direction_to_target(self, target):
        """Asegurar que devuelve enteros"""
        current_pos = self.get_position()
        direction = np.array(target) - np.array(current_pos)

        if abs(direction[0]) > abs(direction[1]):
            return np.array([1 if direction[0] > 0 else -1, 0], dtype=int)
        elif abs(direction[1]) > 0:
            return np.array([0, 1 if direction[1] > 0 else -1], dtype=int)
        else:
            return np.array([0, 0], dtype=int)

    def get_normalized_direction(self):
        """Get the normalized direction vector for this car"""
        if np.linalg.norm(self.velocity) > 0:
            return self.velocity / np.linalg.norm(self.velocity)

        target = self.get_current_target()
        if target is not None:
            current_pos = self.get_position()
            direction = np.array(target) - np.array(current_pos)
            if np.linalg.norm(direction) > 0:
                return direction / np.linalg.norm(direction)

        return np.array([0, 0])

    def find_leader_ahead(self):
        """Encuentra el carro líder adelante en la misma dirección"""
        current_pos = self.get_position()
        my_direction = self.get_normalized_direction()

        if np.linalg.norm(my_direction) == 0:
            return None

        candidates = []

        for other_car in self.intersect.agents:
            if other_car == self:
                continue

            other_pos = other_car.get_position()
            other_direction = other_car.get_normalized_direction()

            vector_to_other = np.array(other_pos) - np.array(current_pos)
            direction_similarity = np.dot(my_direction, other_direction)
            projection = np.dot(vector_to_other, my_direction)

            if direction_similarity > 0.7 and projection > 0:
                perpendicular_distance = np.linalg.norm(vector_to_other - projection * my_direction)

                if perpendicular_distance < 2.0:
                    distance_ahead = projection
                    candidates.append((distance_ahead, other_car))

        if candidates:
            return min(candidates, key=lambda x: x[0])[1]

        return None

    def is_position_occupied(self, target_position):
        """Verifica si una posición está ocupada por otro carro"""
        for other_car in self.intersect.agents:
            if other_car == self:
                continue
            other_pos = other_car.get_position()
            if np.array_equal(other_pos, target_position):
                return True
        return False

    def calculate_safe_velocity(self):
        """Calcula velocidad segura considerando el líder adelante"""
        target = self.get_current_target()
        if target is None:
            return np.array([0, 0], dtype=int)

        desired_velocity = self.calculate_direction_to_target(target)

        # Verificar si la posición de destino está ocupada
        current_pos = self.get_position()
        target_position = tuple(np.array(current_pos) + desired_velocity)

        if self.is_position_occupied(target_position):
            return np.array([0, 0], dtype=int)

        # Buscar líder adelante
        leader = self.find_leader_ahead()

        if leader is None:
            return desired_velocity

        # Calcular distancia al líder
        leader_pos = leader.get_position()
        distance_to_leader = np.linalg.norm(np.array(leader_pos) - np.array(current_pos))

        if distance_to_leader < self.headway_distance:
            return np.array([0, 0], dtype=int)

        elif distance_to_leader < self.headway_distance * 2:
            return desired_velocity if distance_to_leader > self.headway_distance * 1.5 else np.array([0, 0], dtype=int)

        return desired_velocity

    '''
    def get_directional_distance_to_stop(self):
        """Calculate distance to stop position ONLY in the approach direction"""
        current_pos = self.get_position()
        stop_pos = self.stop_positions[self.traffic_light.light_id]
        approach_dir = self.approach_directions[self.traffic_light.light_id]

        direction_to_stop = np.array(stop_pos) - np.array(current_pos)
        directional_distance = np.dot(direction_to_stop, approach_dir)
        return directional_distance
        '''

    # To help stop line dist checks, sets offstep to 1 in the should_stop_for_light
    def get_directional_distance_to_stop(self, offset_stop=1):
        current_pos = self.get_position()
        stop_pos = self.stop_line(offset_stop)
        approach_dir = self.approach_directions[self.traffic_light.light_id]
        return np.dot(np.array(stop_pos) - np.array(current_pos), np.array(approach_dir))

    def is_approaching_from_correct_direction(self):
        """Check if car is approaching from the correct direction"""
        current_pos = self.get_position()
        stop_pos = self.stop_line(offset_stop=1) # Added to help set its stop position
        approach_dir = np.array(self.approach_directions[self.traffic_light.light_id])

        direction_to_stop = np.array(stop_pos) - np.array(current_pos)

        # Checks if moving in same half-plane as approach dir
        if np.linalg.norm(self.velocity) > 0:
            moving_correctly = np.dot(self.velocity, approach_dir) > 0
            return moving_correctly

        return np.dot(direction_to_stop, approach_dir) > 0

    '''def should_stop_for_light(self):
        """Enhanced stopping logic with directional distance"""

        if not self.is_approaching_from_correct_direction():
            return False

        directional_distance = self.get_directional_distance_to_stop()

        if directional_distance <= 0:
            return False

        if directional_distance <= 1.5 and not self.traffic_light.cars_can_move():
            return True

        # Mess w dir distance value to be even further away and stopping
        if self.traffic_light.state == 'yellow':
            if directional_distance <= 3.0:
                return True
            else:
                return False

        if self.traffic_light.state == 'red' and directional_distance <= 3.0:
            return True

        return False'''

    # Checks wheter car should stop for the current light
    def should_stop_for_light(self):
      braking_dist = 3 # Experiment w val to stop close to the stoplight

      if not self.is_approaching_from_correct_direction():
        return False

      directional_distance = self.get_directional_distance_to_stop(offset_stop=1)

      if directional_distance <= 0:
          return False

      # Stop for red lights
      if self.traffic_light.state in ['yellow', 'red_buffer', 'red']:
          # If car is within detection range, stops
          #if directional_distance <= 8.0:
              #return True
          return directional_distance <= braking_dist

      # Also stop at the line if the light doesn't permit movement, just for extra safety
      if directional_distance <= 1.5 and not self.traffic_light.cars_can_move():
          return True

      # Cars can move so just tell cars that they can actually keep moving
      return False

    def update_position(self):
        """Manejar movimiento extendido"""
        target = self.get_current_target()

        if target is None:
            return

        # Check stopping conditions
        if self.should_stop_for_light():
            self.velocity = np.array([0, 0], dtype=int)
            return

        safe_velocity = self.calculate_safe_velocity()

        if np.array_equal(safe_velocity, [0, 0]):
            self.velocity = np.array([0, 0], dtype=int)
            return

        self.velocity = safe_velocity.astype(int)

        if not np.array_equal(self.velocity, [0, 0]):
            try:
                current_pos = self.get_position()
                new_position = tuple(np.array(current_pos) + self.velocity)

                # Verificar límites extendidos
                extended_min = -10
                extended_max = self.intersect.visible_area[0] + 10

                if (extended_min <= new_position[0] <= extended_max and
                    extended_min <= new_position[1] <= extended_max):

                    # Convertir a posición de grilla
                    grid_velocity = self.velocity
                    self.intersect.move_by(self, grid_velocity)

                    # Check if reached target
                    current_pos = self.get_position()
                    if np.allclose(current_pos, target, atol=0.5):
                        self.current_waypoint_index += 1

            except (IndexError, ValueError) as e:
                self.velocity = np.array([0, 0], dtype=int)

    # Added stop line funct to calculate it flexible
    def stop_line(self, offset_stop = 1):
        # Sets stoplight away from the traffic light
        ax, ay = self.approach_directions[self.traffic_light.light_id]
        lx, ly = self.traffic_light.position
        # Calcs where the stoplight should be based on the dir
        return (lx - ax*offset_stop, ly - ay*offset_stop)


# Intersection enviornment

In [8]:
class Intersection(ap.Grid):
    def setup(self):
        pass

# Intersection model

In [9]:
# Intersection model
class EnhancedIntersectModel(ap.Model):
    def setup(self):
        p = self.p # Assign intersection params to itself

        size = self.p.size
        # Usar ExtendedIntersection en lugar de Intersection
        self.intersect = ExtendedIntersection(self, shape=(size, size))

        # Create traffic lights with minimum green times for adaptive control
        self.traffic_lights = {
            1: TrafficLight(self, light_id=1, position=(12, 22), green_time=p.l1_green, min_green_time=p.l1_min_green),
            2: TrafficLight(self, light_id=2, position=(8, 12), green_time=p.l2_green, min_green_time=p.l2_min_green),
            3: TrafficLight(self, light_id=3, position=(16, 8), green_time=p.l3_green, min_green_time=p.l3_min_green),
            4: TrafficLight(self, light_id=4, position=(20, 18), green_time=p.l4_green, min_green_time=p.l4_min_green) # MOVED 2 unit to left from (22, 18)
        }

        #self.setup_light_sequence() # COMMENTING FOR NOW
        self.paths = self.create_paths()

        # Initialize the enhanced spawner
        self.car_spawner = EnhancedCarSpawner(self)

        # Adding to hopefully make it flexible
        self.current_active_light = 1 # Starts w the first light active
        self.traffic_lights[1].should_be_active = True # Gets the first traffic light from dictionary
        self.light_sequence = [1, 2, 3, 4] # Order of the lights

    def setup_light_sequence(self):
        for light_id, light in self.traffic_lights.items():
            if light_id == 1:
                light.timer = 0
                light.state = 'green'
            else:
                light.timer = light.cycle_time
                light.state = 'red'

    def create_paths(self):
        paths = {}

        # Traffic Light 1 paths (Purple)
        paths[1] = Path(1, 1, [(12, 24), (12, 22), (12, 20), (12, 18), (10, 16), (8, 16), (0, 16)], 'left')
        paths[2] = Path(2, 1, [(12, 25), (12, 0)], 'straight')
        paths[3] = Path(3, 1, [(12, 26), (12, 22), (12, 20), (12, 18), (14, 16), (16, 14), (29, 14)], 'right')

        # Traffic Light 2 paths (Yellow)
        paths[4] = Path(4, 2, [(7, 12), (10, 12), (12, 14), (14, 16), (14, 17), (14, 20), (14, 26)], 'left')
        paths[5] = Path(5, 2, [(6, 12), (10, 12), (14, 12), (16, 14), (18, 14), (29, 14)], 'straight')
        paths[6] = Path(6, 2, [(5, 12), (10, 12), (12, 12), (12, 10), (12, 0)], 'right')

        # Traffic Light 3 paths (Red)
        paths[7] = Path(7, 3, [(16, 7), (16, 13), (14, 14), (12, 15), (10, 16), (8, 16), (0, 16)], 'left')
        paths[8] = Path(8, 3, [(16, 6), (16, 13), (15, 15), (14, 16), (14, 18), (14, 26)], 'straight')
        paths[9] = Path(9, 3, [(16, 5), (16, 13), (17, 13), (18, 14), (19, 14), (29, 14)], 'right')
        paths[10] = Path(10, 3, [(16, 4), (18, 4), (19, 3), (20, 0)], 'u-turn')

        # Traffic Light 4 paths (Blue)
        paths[11] = Path(11, 4, [(22, 18), (18, 18), (16, 17), (14, 16), (12, 12), (12, 10), (12, 0)], 'left')
        paths[12] = Path(12, 4, [(23, 18), (18, 18), (12, 18), (10, 16), (8, 16), (0, 16)], 'straight')
        paths[13] = Path(13, 4, [(24, 18), (18, 18), (16, 19), (14, 20), (14, 22), (14, 26)], 'right')

        return paths

    def step(self):
        # Spawn new cars dynamically
        self.car_spawner.spawn_cars()

        # Update traffic light sequence
        #self.update_traffic_light_sequence() # Old swaps
        #self.adaptive_light_update() # new w heuristic
        self.adaptive_light_controller()

        # Update cars and remove completed ones
        cars_to_remove = []
        for car in self.intersect.agents:
            car.update_position()
            if car.get_current_target() is None:
                cars_to_remove.append(car)

        if cars_to_remove:
            self.intersect.remove_agents(cars_to_remove)


    def update_traffic_light_sequence(self):
        total_cycle_time = sum(light.cycle_time for light in self.traffic_lights.values())
        cycle_position = self.t % total_cycle_time

        cumulative_time = 0
        active_light_id = 1

        for light_id in [1, 2, 3, 4]:
            light = self.traffic_lights[light_id]
            if cycle_position < cumulative_time + light.cycle_time:
                active_light_id = light_id
                break
            cumulative_time += light.cycle_time

        for light_id, light in self.traffic_lights.items():
            if light_id == active_light_id:
                light.update_state()
            else:
                light.state = 'red'
                light.timer = 0


    # Help count cars incoming from which dir based on light id
    def count_stoplight_cars(self, light_id):
        counter = 0
        light = self.traffic_lights[light_id] # Just retrieves curr light whose id is passed as param

        # Approach dirs for each light
        approach_directions = {
            1: (0, -1), # Moving N->S = -1 down
            2: (1, 0), # Moving W->E = 1 right
            3: (0, 1), # Moving S->N = 1 up
            4: (-1, 0) # Moving E->W = -1 left
        }

        ax, ay = approach_directions[light_id] # Gets the appropiate approach in x and y
        stop_pos = (light.position[0] - ax*1, light.position[1] - ay*1)  # Uses 1 cell as offset, if modify it change it here
        approach_dir = np.array([ax, ay])

        # Begin counting
        for car in self.intersect.agents:
            # Skips counting cars that are not necessary
            if car.traffic_light.light_id != light_id:
                continue
            # Car is part of it, gets its position and dist to light should be within 8 blocks
            car_pos = np.array(car.get_position())
            d = np.dot(np.array(stop_pos) - car_pos, approach_dir)
            if 0 < d <= 8:
                counter += 1

        return counter

    # Adaptive controller w heuristic
    def adaptive_light_controller(self):
        # Get line counts for all lights
        line_counts = {
          1: self.count_stoplight_cars(1),
          2: self.count_stoplight_cars(2),
          3: self.count_stoplight_cars(3),
          4: self.count_stoplight_cars(4)
        }

        # Moves light to next stage since its start
        for light in self.traffic_lights.values():
            light.update_state()

        current_light = self.traffic_lights[self.current_active_light]
        next_light_id = (self.current_active_light % 4) + 1 # Using mod so that I can compare light 4 to 1 (4%4=0+1=1)

        # Adaptive heuristic logic, isolates counts for curr line and the next one
        thresh_diff = 1 # Threshold val to update it (so rn this means next_line needs 2 more cars)
        current_line = line_counts[self.current_active_light]
        next_line = line_counts[next_light_id]

        # Makes sure curr light is green so that it doesn't skip thru any of the other phases
        if current_light.state == 'green':
            # Checks if min time already passed and next line is longer than curr line w threshold considered so that it can swap
            if (current_light.time_in_state > current_light.min_green_time and next_line > current_line + thresh_diff):
                msg = f"Early switch from {self.current_active_light} to {next_light_id}: {current_line} vs {next_line} cars; time {current_light.time_in_state}$"
                print(f"\t{msg}")
                Server.send_message(msg)
                current_light.force_switch()

        # If active done w cycle, calc next one and set as active
        if current_light.state == 'red' and not current_light.should_be_active:
            self.current_active_light = next_light_id
            self.traffic_lights[self.current_active_light].should_be_active = True


        '''
        # Adaptive logic only during green
        if current_light.state == 'green':
            # Extend if light has more cars in line than next one, and not yet in max time
            if (current_line > next_line + thresh_diff and current_light.time_in_state < current_light.green_time):
                print(f"Extending Light {self.current_active_light}: {current_line} vs {next_line} cars")

            # Early switch if already min time passed and other one has more line
            elif (current_light.time_in_state >= current_light.min_green_time and next_line > current_line + thresh_diff):
                print(f"Early switch from {self.current_active_light} to {next_light_id}: {current_line} vs {next_line} cars; time {current_light.time_in_state}") # Shows swap and what time it was to see if it followed thru on the time that it needed to run
                current_light.force_switch() # Calls funct to force the switch if appropiate


        # Checks if light is done w cycle to activate the next one in the sequence
        if (current_light.state == 'red' and not current_light.should_be_active):
            self.current_active_light= next_light_id
            self.traffic_lights[self.current_active_light].should_be_active = True
            print(f"----\nNow activating light {self.current_active_light}")

        # Update all lights, manages its own progression
        for light in self.traffic_lights.values():
            light.update_state()
        '''



# Animation

In [10]:
# Animation
total_paths = 13

def animation_plot_single(m, ax):
    ax.clear()
    ax.set_title(f"Enhanced Traffic Intersection - Step t={m.t}")

    # Mantener el área visible original
    visible_size = m.p.size
    ax.set_xlim(-1, visible_size)
    ax.set_ylim(-1, visible_size)

    ax.set_xticks(range(0, visible_size, 2))
    ax.set_yticks(range(0, visible_size, 2))

    # Draw paths
    path_colors = {1: 'purple', 2: 'mediumorchid', 3: 'darkviolet',
                   4: 'khaki', 5:'gold', 6: 'yellow',
                   7: 'indianred', 8: 'brown', 9: 'firebrick', 10: 'darkred',
                   11: 'deepskyblue', 12: 'dodgerblue', 13: 'royalblue'}

    for path_id, path in m.paths.items():
        if path_id <= total_paths:
            color = path_colors[path_id]
            waypoints = np.array(path.waypoints)
            ax.plot(waypoints[:, 0], waypoints[:, 1], '--',
                   color=color, alpha=0.7, linewidth=2)

    # Draw traffic lights
    light_colors = {'green': 'green', 'flash': 'lightgreen', 'yellow': 'yellow', 'red_buffer':'red', 'red': 'red'}

    for light_id, light in m.traffic_lights.items():
        color = light_colors[light.state]
        # Number the light ids to make it easier to see
        ax.scatter(*light.position, s=150, marker='s', c=color,
                  edgecolor='black', linewidth=2)

        # Add light ID text to make it easier to see
        ax.text(light.position[0], light.position[1], str(light_id),
               ha='center', va='center', fontweight='bold', fontsize=10)
        # Show light state and time running
        ax.text(light.position[0], light.position[1]-1, f'{light.state}\n({light.time_in_state})',
               ha='center', va='top', fontsize=8)

    # Draw cars solo si están en área visible
    for car in m.intersect.agents:
        pos = car.get_position()

        # Solo dibujar si está en área visible
        if (0 <= pos[0] <= visible_size and 0 <= pos[1] <= visible_size):
            if car.velocity[1] > 0:
                marker = '^'
            elif car.velocity[1] < 0:
                marker = 'v'
            elif car.velocity[0] > 0:
                marker = '>'
            elif car.velocity[0] < 0:
                marker = '<'
            else:
                marker = 'o'

            ax.scatter(*pos, s=120, marker=marker, c='black', edgecolor='red', linewidth=2)

    ax.grid(True, alpha=0.3)

def animation_plot(m, p):
    fig = plt.figure(figsize=(5, 5))
    ax = fig.add_subplot(111)
    animation = ap.animate(m(p), fig, ax, animation_plot_single)
    return IPython.display.HTML(animation.to_jshtml(fps=3))

# Run model

In [12]:
# Parameters
parameters = {
    'size': 30,
    'steps': 100,
    # TIMING
    ## Traffic light max green times
    'l1_green': 19,
    'l2_green': 28,
    'l3_green': 8,
    'l4_green': 27,
    # Min times
    'l1_min_green': 6,
    'l2_min_green': 9,
    'l3_min_green': 5,
    'l4_min_green': 9,
}

model = EnhancedIntersectModel(parameters)
animation_plot(EnhancedIntersectModel, parameters)

	Spawn 13 (right) from east at (38, 18)$
	Spawn 7 (left) from south at (16, -8)$
	Spawn 2 (straight) from north at (12, 38)$
	Spawn 9 (right) from south at (16, -8)$
	Spawn 8 (straight) from south at (16, -8)$
	Spawn 1 (left) from north at (12, 38)$
	Spawn 4 (left) from west at (-8, 12)$
	Spawn 8 (straight) from south at (16, -8)$
	Spawn 3 (right) from north at (12, 38)$
	Spawn 12 (straight) from east at (38, 18)$
	Spawn 5 (straight) from west at (-8, 12)$
	Spawn 6 (right) from west at (-8, 12)$
	Spawn 10 (u-turn) from south at (16, -8)$
	Spawn 5 (straight) from west at (-8, 12)$
	Spawn 5 (straight) from west at (-8, 12)$
	Spawn 7 (left) from south at (16, -8)$
	Spawn 2 (straight) from north at (12, 38)$
	Spawn 5 (straight) from west at (-8, 12)$
	Spawn 11 (left) from east at (38, 18)$
	Early switch from 2 to 3: 1 vs 3 cars; time 14$
	Spawn 8 (straight) from south at (16, -8)$
	Spawn 2 (straight) from north at (12, 38)$
	Spawn 9 (right) from south at (16, -8)$
	Spawn 2 (straight) from 